<a href="https://colab.research.google.com/github/ArjunJSP/quantities/blob/main/testquantities.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **QUANTITIES CALCULATOR: Roper St. Francis Hospital**

# Import .e2k File and Setup Calculator

Mount to Drive Location and double check files in the directory


In [112]:
from google.colab import drive
drive.mount('/content/drive')

# Navigate to a specific folder in your Google Drive
%cd /content/drive/My Drive/mountlocation

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/My Drive/mountlocation


Import necessary libraries

In [113]:
import numpy as np
import pandas as pd
from io import StringIO
import re #currently not using
import shlex
import math
import matplotlib.pyplot as plt
import warnings
from openpyxl import load_workbook
from google.colab import data_table
from vega_datasets import data
# pip install XlsxWriter
# import xlsxwriter
from IPython.core.display import display, HTML

data_table.enable_dataframe_formatter()

Define file path:

In [114]:
filepath = 'RSFH_PODIUM_V11.0.4.e2k'
#Export units for e2k file:
fileunit_length = 'in'
fileunit_weight = 'kip'

# Redefine ETABS .e2k as Dataframes



Computed dataframes include:
>**df_stories**: individual story heights and cumulative elevation in default .e2k units<br>**df_pointcoordinates**: x,y coordinates for each *point label* (note: these labels might be repeated on several stories that share geometry)<br>**df_lineconnectivity**: defines the element type, start and end point label (note: elements that repeat across levels will share a label) <br>**df_areaconnectivity**: defines the element type, point label corners <br>**df_groupassigns**: defines group for each element label (note: groups are associated with element labels, not unique elements) <br>**df_lineassigns**: defines each line based on its label *and* the story it exists on (note: this is currently the most comprehensive df that includes a list entry for every line element in the model) <br>**df_areaassigns**: defines each area based on its label *and* the story it exists on (note: this is currently the most comprehensive df that includes a list entry for every area element in the model)


## Open text file and identify $ headers

In [115]:
with open(filepath, 'r') as file:
    # Initialize lists to store data
    dollar_lines = []
    line_indices = []
    line_lengths = []

    # Initialize variables
    after_dollar = False
    line_count = 0

    # Read each line in the file
    for idx, line in enumerate(file):
        # Skip the line "$ END OF MODEL FILE"
        if line.strip() == "$ END OF MODEL FILE":
            continue

        # Check if the line starts with '$'
        if line.startswith('$'):
            # Set the flag to True indicating that we are currently reading lines after the '$' line
            after_dollar = True
            # Append the line to the list of dollar lines
            dollar_lines.append(line.strip())
            # Append the index of the line
            line_indices.append(idx)
            # Reset line count
            line_count = 0
        # Check if we are currently reading lines after the '$' line and we encounter a blank line
        elif after_dollar and line.strip() == '':
            # If so, append the line count to the list of line lengths
            line_lengths.append(line_count)
            # Reset the flag indicating that we are no longer reading lines after the '$' line
            after_dollar = False
        # Increment the line count if we are currently reading lines after the '$' line
        elif after_dollar:
            line_count += 1

# Create a DataFrame from the collected data
Data_Indexes = pd.DataFrame({'Line': dollar_lines, 'Index': line_indices, 'Length': line_lengths})

# Print the DataFrame
Data_Indexes


Line  Index  Length
0   $ File C:\Users\arjun.prihar\Documents\RFSH\PO...      0       0
1                               $ PROGRAM INFORMATION      2       1
2                                          $ CONTROLS      5       5
3                    $ STORIES - IN SEQUENCE FROM TOP     12       4
4                                             $ GRIDS     18      26
5                                   $ DIAPHRAGM NAMES     46       4
6                               $ MATERIAL PROPERTIES     52     149
7                                 $ REBAR DEFINITIONS    203      12
8                                    $ FRAME SECTIONS    217     439
9                         $ AUTO SELECT SECTION LISTS    658      30
10                                $ CONCRETE SECTIONS    690      13
11                                  $ TENDON SECTIONS    705       1
12                                  $ SLAB PROPERTIES    708       8
13                                  $ DECK PROPERTIES    718       6
14                                  $ WALL PROPERTIES    726       6
15                                  $ LINK PROPERTIES    734       3
16                            $ PANEL ZONE PROPERTIES    739       2
17                              $ PIER/SPANDREL NAMES    743       2
18                                $ POINT COORDINATES    747     479
19                              $ LINE CONNECTIVITIES   1228     777
20                              $ AREA CONNECTIVITIES   2007     170
21                                           $ GROUPS   2179    2050
22                                    $ POINT ASSIGNS   4231    1162
23                                     $ LINE ASSIGNS   5395    2240
24                                     $ AREA ASSIGNS   7637     414
25                                    $ LOAD PATTERNS   8053     120
26                               $ POINT OBJECT LOADS   8175       4
27                               $ FRAME OBJECT LOADS   8181     122
28                          $ SHELL UNIFORM LOAD SETS   8305     183
29                               $ SHELL OBJECT LOADS   8490     414
30                                 $ ANALYSIS OPTIONS   8906       4
31                                      $ MASS SOURCE   8912      20
32                                        $ FUNCTIONS   8934      43
33                        $ GENERALIZED DISPLACEMENTS   8979       0
34                                       $ LOAD CASES   8981     172
35                                $ LOAD COMBINATIONS   9155    1574
36                         $ STEEL DESIGN PREFERENCES  10731      11
37                          $ STEEL DESIGN OVERWRITES  10744    2898
38                      $ CONCRETE DESIGN PREFERENCES  13644       7
39                     $ COMPOSITE DESIGN PREFERENCES  13653      15
40              $ COMPOSITE COLUMN DESIGN PREFERENCES  13670       7
41                          $ WALL DESIGN PREFERENCES  13679       6
42                 $ CONCRETE SLAB DESIGN PREFERENCES  13687       4
43                                  $ DIMENSION LINES  13693       1
44                                       $ TABLE SETS  13696       0
45                        $ DATABASE TABLE NAMED SETS  13698     178
46                              $ PROJECT INFORMATION  13878       1
47                                              $ LOG  13881    1542

###Table-Pulling Function

---



In [116]:
def get_table(table_name, file_name):
  start_index = 1 + Data_Indexes.loc[Data_Indexes['Line'] == table_name, 'Index'].iloc[0]
  end_index = start_index + Data_Indexes.loc[Data_Indexes['Line'] == table_name, 'Length'].iloc[0] -1

  with open(file_name, 'r') as file:
      # Initialize a list to store the extracted lines
      extracted_lines = []

      # Read each line in the file
      for idx, line in enumerate(file):
          # Check if the current index is within the range of the specified indices
          if start_index <= idx <= end_index:
              # Add the line to the list of extracted lines
              extracted_lines.append(line.strip())

  data_array = extracted_lines
  data_list = []

  #__________
  # #define a function that splits along spaces AND between entries bounded by "", so that Group Names can have spaces within them, but not cause splitting issues

  def split_quoted_string(s):
      # Use shlex to split the string respecting quoted substrings
      parts = shlex.split(s)

      # Filter out empty strings
      parts = [part for part in parts if part]

      return parts
  #__________


  # Iterate over each string in the array
  for line in extracted_lines:
      # Split the string based on space delimiters
      # split_line = line.split()
      split_line = split_quoted_string(line)
      # Append the split line to the list of data
      data_list.append(split_line)

  # Create a DataFrame from the list of data
  df = pd.DataFrame(data_list)
  return df

##Story Heights
> df_stories

In [117]:
df = get_table('$ STORIES - IN SEQUENCE FROM TOP',filepath)

df = df[[1, 3]]
df.columns = ['Level','Height']
#height is reported in inches

# Remove quotation marks from data
for column in df.columns:
  df[column] = df[column].str.replace('"', '')

# Convert 'Height' column values from string to integer
df['Height'] = df['Height'].astype(int)

# Reverse the order of the column 'values'
reversed_values = df['Height'][::-1]

# Calculate the reverse cumulative sum
df['Elevation'] = reversed_values.cumsum()[::-1]

df_stories = df
df_stories

Level  Height  Elevation
0   L03     240        672
1   L02     228        432
2   L01     204        204
3   L00       0          0

## Find Point Coordinates
> df_pointcoordinates



In [118]:
df3 = get_table('$ POINT COORDINATES',filepath)

df3 = df3[[1, 2, 3]]
df3.columns = ['PointID','x','y']

# Remove quotation marks from data
for column in df3.columns:
  df3[column] = df3[column].str.replace('"', '')
df_pointcoordinates = df3
df_pointcoordinates

PointID          x          y
0         1  -5902.142  -5161.223
1         2  -5902.142  -4771.223
2         3  -6292.142  -4771.223
3         4  -6292.142  -5161.223
4         5  -6292.142  -4015.223
..      ...        ...        ...
474     475  -5713.142  -4393.223
475     488  -6097.142  -3763.223
476     489  -6097.142  -3133.223
477     490  -6097.142  -3007.223
478     491  -6097.142  -2377.223

[479 rows x 3 columns]

## Find Line Connectivities
>df_lineconnectivity

In [119]:
df2 = get_table('$ LINE CONNECTIVITIES', filepath)

df2 = df2[[1, 2, 3, 4, 5]]
df2.columns = ['ElemID','ElemType','iPointID','jPointID', 'MultiLevel']
# Multi Level Refers to a true/false if the element spans multiple floors, ie. a Column or Brace extends from its Level assignment down to the elevation of the level below.

# Remove quotation marks from data
for column in df2.columns:
  df2[column] = df2[column].str.replace('"', '')

df2['MultiLevel'] = df2['MultiLevel'].astype(int)

df_lineconnectivity = df2

df_lineconnectivity.to_csv('df_lineconnectivity.txt', sep='\t', index=False)

df_lineconnectivity

ElemID ElemType iPointID jPointID  MultiLevel
0       C1   COLUMN       34       34           1
1       C2   COLUMN       33       33           1
2       C3   COLUMN       54       54           1
3       C4   COLUMN       61       61           1
4       C5   COLUMN       75       75           1
..     ...      ...      ...      ...         ...
772    D88    BRACE      139      473           1
773    D89    BRACE       26      474           1
774    D90    BRACE      148      474           1
775    D91    BRACE        7      475           1
776    D92    BRACE      138      475           1

[777 rows x 5 columns]

## Find Area Connectivities
>df_areaconnectivity

In [120]:
df2 = get_table('$ AREA CONNECTIVITIES',filepath)

df2 = df2[[1, 2, 4, 5, 6, 7]]
df2.columns = ['ElemID','ElemType','iPointID','jPointID','kPointID','lPointID']

# Remove quotation marks from data
for column in df2.columns:
  df2[column] = df2[column].str.replace('"', '')
df_areaconnectivity = df2
df_areaconnectivity

ElemID ElemType iPointID jPointID kPointID lPointID
0       F1    FLOOR        1        2        3        4
1       F2    FLOOR        5        6        7        8
2       F3    FLOOR        8        9       10        5
3       F4    FLOOR        9       11       12       10
4       F5    FLOOR       13       12       11       14
..     ...      ...      ...      ...      ...      ...
165   F166    FLOOR      130      131      146      145
166   F167    FLOOR      147      146      131      132
167   F168    FLOOR      133      148      147      132
168   F169    FLOOR      149      148      133      134
169   F170    FLOOR      108      109      124      123

[170 rows x 6 columns]

## Find Group Assignments
>df_groupassigns


In [121]:
df = get_table('$ GROUPS',filepath)
df = df[[1, 3, 4]]
# df.rename(columns={1: 'FrameID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

#reanme dataframe columns
df.columns = ['Group','ElemID','Level']

df_groupassigns = df
df_groupassigns.to_csv('df_groupassigns.txt', sep='\t', index=False)

df_groupassigns

Group ElemID Level
0            MF   None  None
1          CLAD   None  None
2         MF-3x   None  None
3      MF-Rigid   None  None
4         GR. B   None  None
...         ...    ...   ...
2045  Grade Bm.   B271   L00
2046  Grade Bm.   B272   L00
2047  Grade Bm.   B273   L00
2048  Grade Bm.   B274   L00
2049  Grade Bm.   B275   L00

[2050 rows x 3 columns]

## Find Line Assigns
>df_lineassigns

In [122]:
df = get_table('$ LINE ASSIGNS',filepath)
# Create a DataFrame from the list of data
# df = pd.DataFrame(data_list)
df = df[[1, 2, 4]]
df.rename(columns={1: 'FrameID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

# Calculate the midpoint index
midpoint_index = len(df) # // 2

# Crop the DataFrame in half
df_lineassigns = df.iloc[:midpoint_index]
df_lineassigns.columns = ['ElemID','Level','Section']

df_lineassigns.to_csv('lineassigns.txt', sep='\t', index=False)

df_lineassigns

ElemID Level      Section
0        B1   L00  B24X24-6KSI
1        B2   L00  B24X24-6KSI
2        B3   L00  B24X24-6KSI
3        B4   L00  B24X24-6KSI
4        B5   L00  B24X24-6KSI
...     ...   ...          ...
2235    D74   L03        -7.85
2236    D79   L03        -10.4
2237    D80   L03        -10.4
2238    D81   L03        -10.4
2239    D82   L03        -10.4

[2240 rows x 3 columns]

## Find Area Assigns
>df_areaassigns

In [123]:
df = get_table('$ AREA ASSIGNS',filepath)
# Create a DataFrame from the list of data
# df = pd.DataFrame(data_list)
df = df[[1, 2, 4]]
df.rename(columns={1: 'AreaID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

# # Calculate the midpoint index
# midpoint_index = len(df) // 2

# Crop the DataFrame in half
df_areaassigns = df.iloc[:midpoint_index]
df_areaassigns.columns = ['ElemID','Level','Section']
df_areaassigns

ElemID Level             Section
0       F1   L00              RS1-10
1       F2   L00              RS1-10
2       F3   L00              RS1-10
3       F4   L00              RS1-10
4       F5   L00              RS1-10
..     ...   ...                 ...
409   F166   L03  roof_deck_unfilled
410   F167   L03  roof_deck_unfilled
411   F168   L03  roof_deck_unfilled
412   F169   L03  roof_deck_unfilled
413   F170   L03  roof_deck_unfilled

[414 rows x 3 columns]

#Assemble Frame Quantity Table


- associating the element assignment with its section, group, connectivity, and AISC unit weight.
- setting non-standard AISC section weights to zero (will need manual assignmnents)
>df_lines

## Referencing the AISC Excel Table
>df_AISC

In [124]:
steel_dbs= {'AISC v15.0':
 {'file_path':
  "/content/drive/Shareddrives/Firm-wide Structural Resources/02.General Project Resources/02.06.Spreadsheets/02.06.09 Analysis-Steel/AISC v15 Shapes Database.xlsx",
  'sheet_name': "Database v15.0",
  'US': 'A:CF',
  'Metric': ['A, CG:FJ']}}

STEEL_DB = 'AISC v15.0'
UNITS = 'US'

df_AISC = pd.read_excel(steel_dbs[STEEL_DB]['file_path'],
                         sheet_name=steel_dbs[STEEL_DB]['sheet_name'],
                         usecols=steel_dbs[STEEL_DB][UNITS],
                         header=0)

df_AISC
# #using the .at function to lookup values in the section database and then .loc to find information about that section, ie. the weight ('W') based on steeel)_db database column labels
# member_section.at[1,'Section']
# #note: this will break for NONE sections!
# steel_db.loc[steel_db['AISC_Manual_Label']== (member_section.at[1,'Section']),'W'].values[0]

Type EDI_Std_Nomenclature AISC_Manual_Label T_F       W       A     d  \
0        W              W44X335           W44X335   F  335.00   98.50    44   
1        W              W44X290           W44X290   F  290.00   85.40  43.6   
2        W              W44X262           W44X262   F  262.00   77.20  43.3   
3        W              W44X230           W44X230   F  230.00   67.80  42.9   
4        W              W40X655           W40X655   T  655.00  193.00  43.6   
...    ...                  ...               ...  ..     ...     ...   ...   
2086  PIPE             Pipe5XXS          Pipe5XXS   F   38.60   10.70     –   
2087  PIPE             Pipe4XXS          Pipe4XXS   F   27.60    7.66     –   
2088  PIPE             Pipe3XXS          Pipe3XXS   F   18.60    5.17     –   
2089  PIPE         Pipe2-1/2XXS      Pipe2-1/2XXS   F   13.70    3.83     –   
2090  PIPE             Pipe2XXS          Pipe2XXS   F    9.04    2.51     –   

        ddet Ht  h  ...   rts    ho   PA PA2   PB   PC   PD   T  WGi WGo  
0         44  –  –  ...  4.24  42.2  132   –  148  104  120  38  5.5   –  
1     43.625  –  –  ...   4.2    42  131   –  147  103  119  38  5.5   –  
2      43.25  –  –  ...  4.17  41.9  131   –  147  102  118  38  5.5   –  
3     42.875  –  –  ...  4.13  41.7  130   –  146  102  118  38  5.5   –  
4     43.625  –  –  ...  4.71  40.1  132   –  149  104  121  34  7.5   –  
...      ... .. ..  ...   ...   ...  ...  ..  ...  ...  ...  ..  ...  ..  
2086       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2087       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2088       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2089       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2090       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  

[2091 rows x 84 columns]

## Assembly of df_lines

In [125]:
#merge the line assignments (comprised of a value entry for each line label in the model) with the line connectivity (describing how that line connects to joint labels)
#note: the labels are not unique IDs; each line label can represent multiple lines that are identical across multiple floors

df_lines = pd.merge(df_lineassigns,df_lineconnectivity, on='ElemID')

#merge the line data with group assignments
#note: since line labels can be repeated across floors, the merge must use two keys: the line label (ElemID) and the level it is on (Level)

df_lines = pd.merge(df_lines, df_groupassigns, on=['ElemID','Level'])

#merge the line data with AISC weight information for that section
#note: if section is not in AISC table, weight (W) is assigned as zero (0) NOTE: weight in AISC table is in lbs/ft

df_lines = pd.merge(df_lines, df_AISC[['AISC_Manual_Label','W']], left_on = 'Section', right_on = 'AISC_Manual_Label', how='left', indicator=True)
df_lines = df_lines.replace(np.nan, 0)

#save df to text file for review
df_lines.to_csv('merged_output.txt', sep='\t', index=False)

#preview dataframe
df_lines


ElemID Level      Section ElemType iPointID jPointID  MultiLevel  \
0        B1   L00  B24X24-6KSI     BEAM       33       34           0   
1        B2   L00  B24X24-6KSI     BEAM       61       33           0   
2        B3   L00  B24X24-6KSI     BEAM       76       61           0   
3        B4   L00  B24X24-6KSI     BEAM       91       76           0   
4        B5   L00  B24X24-6KSI     BEAM      106       91           0   
...     ...   ...          ...      ...      ...      ...         ...   
2235    D74   L03        -7.85    BRACE      111      467           1   
2236    D79   L03        -10.4    BRACE      147      470           1   
2237    D80   L03        -10.4    BRACE      146      470           1   
2238    D81   L03        -10.4    BRACE      148      471           1   
2239    D82   L03        -10.4    BRACE      147      471           1   

          Group AISC_Manual_Label    W     _merge  
0     Grade Bm.                 0  0.0  left_only  
1     Grade Bm.                 0  0.0  left_only  
2     Grade Bm.                 0  0.0  left_only  
3     Grade Bm.                 0  0.0  left_only  
4     Grade Bm.                 0  0.0  left_only  
...         ...               ...  ...        ...  
2235        BRB                 0  0.0  left_only  
2236        BRB                 0  0.0  left_only  
2237        BRB                 0  0.0  left_only  
2238        BRB                 0  0.0  left_only  
2239        BRB                 0  0.0  left_only  

[2240 rows x 11 columns]

In [126]:
#~~~needs to be rewritten to delete duplicate data in order to run multiple times

#merge df_lines key:iPointID with df_pointcoordinates key:PointID to find x,y of that point (rename column: ix, iy) and set iz = 0
#merge df_lines key:jPointID with df_pointcoordinates key:PointID to find x,y of that point (rename column: jx, jy)
#if Multilevel > 0, assign jz as the pd.merge values in df_stories key:Level
#calculate vector distance between (ix,iy, iz) and (jx, jy, jz)

###import ix, iy, set iz to zero
df_lines = pd.merge(df_lines, df_pointcoordinates, left_on = 'iPointID', right_on = 'PointID')
df_lines = df_lines.rename(columns={'x': 'ix', 'y': 'iy'})
df_lines['iz'] = 0

###import jx, jy, import jz
df_lines = pd.merge(df_lines, df_pointcoordinates, left_on = 'jPointID', right_on = 'PointID')
df_lines = pd.merge(df_lines, df_stories[['Level','Height']], on='Level')
df_lines = df_lines.rename(columns={'x': 'jx', 'y': 'jy', 'Height':'jz'})
df_lines[['MultiLevel','ix', 'iy', 'iz', 'jx', 'jy', 'jz']] = df_lines[['MultiLevel','ix', 'iy', 'iz', 'jx', 'jy', 'jz']].astype(float)

df_lines.loc[df_lines['MultiLevel'] == 0, 'jz'] = 0

###define function to calculate vector distance of element
def calculate_distance(row):
    x1, y1, z1 = row['ix'], row['iy'], row['iz']
    x2, y2, z2 = row['jx'], row['jy'], row['jz']
    distance = np.sqrt((x2 - x1)**2 + (y2 - y1)**2 + (z2 - z1)**2)
    return distance

#Apply function to each row
df_lines['Length'] = df_lines.apply(calculate_distance, axis=1)

#if e2k file length units are inches, divide W by 12 to get unit weight in inches.
#compute weight of element, given AISC default 'W' weight units are lb/ft

length_conversion = 1
if fileunit_length == 'in':
  length_conversion = 1/12

df_lines['W'] = df_lines['W']*length_conversion

weight_conversion = 1
if fileunit_weight == 'kip':
  weight_conversion = 1/1000

df_lines['W'] = df_lines['W']*weight_conversion

df_lines


ElemID Level      Section ElemType iPointID jPointID  MultiLevel  \
0        B1   L00  B24X24-6KSI     BEAM       33       34         0.0   
1        B2   L00  B24X24-6KSI     BEAM       61       33         0.0   
2        B3   L00  B24X24-6KSI     BEAM       76       61         0.0   
3        B4   L00  B24X24-6KSI     BEAM       91       76         0.0   
4        B5   L00  B24X24-6KSI     BEAM      106       91         0.0   
...     ...   ...          ...      ...      ...      ...         ...   
2235    D74   L03        -7.85    BRACE      111      467         1.0   
2236    D79   L03        -10.4    BRACE      147      470         1.0   
2237    D80   L03        -10.4    BRACE      146      470         1.0   
2238    D81   L03        -10.4    BRACE      148      471         1.0   
2239    D82   L03        -10.4    BRACE      147      471         1.0   

          Group AISC_Manual_Label    W     _merge PointID_x        ix  \
0     Grade Bm.                 0  0.0  left_only        33 -3256.141   
1     Grade Bm.                 0  0.0  left_only        61 -3634.141   
2     Grade Bm.                 0  0.0  left_only        76 -4012.141   
3     Grade Bm.                 0  0.0  left_only        91 -4390.142   
4     Grade Bm.                 0  0.0  left_only       106 -4768.142   
...         ...               ...  ...        ...       ...       ...   
2235        BRB                 0  0.0  left_only       111 -4768.142   
2236        BRB                 0  0.0  left_only       147 -5524.142   
2237        BRB                 0  0.0  left_only       146 -5524.142   
2238        BRB                 0  0.0  left_only       148 -5524.142   
2239        BRB                 0  0.0  left_only       147 -5524.142   

             iy   iz PointID_y        jx         jy     jz      Length  
0    -5161.2230  0.0        34 -2932.141 -5161.2230    0.0  324.000000  
1    -5161.2230  0.0        33 -3256.141 -5161.2230    0.0  378.000000  
2    -5161.2230  0.0        61 -3634.141 -5161.2230    0.0  378.000000  
3    -5161.2230  0.0        76 -4012.141 -5161.2230    0.0  378.001000  
4    -5161.2230  0.0        91 -4390.142 -5161.2230    0.0  378.000000  
...         ...  ...       ...       ...        ...    ...         ...  
2235 -3259.2230  0.0       467 -4768.142 -3070.2230  240.0  305.484861  
2236  -991.2232  0.0       470 -5524.142 -1180.2230  240.0  305.484737  
2237 -1369.2230  0.0       470 -5524.142 -1180.2230  240.0  305.484861  
2238  -613.2232  0.0       471 -5524.142  -802.2232  240.0  305.484861  
2239  -991.2232  0.0       471 -5524.142  -802.2232  240.0  305.484861  

[2240 rows x 20 columns]

# Assemble Area Quantity Table

In [127]:
#merge the area assignments (comprised of a value entry for each line label in the model) with the area connectivity (describing how that line connects to joint labels)
#note: the labels are not unique IDs; each line label can represent multiple lines that are identical across multiple floors

df_areas = pd.merge(df_areaassigns,df_areaconnectivity, on='ElemID')

In [128]:
###import ix, iy
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'iPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'ix', 'y': 'iy'}).drop(['PointID'], axis=1)


In [129]:

# ###import jx, jy
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'jPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'jx', 'y': 'jy'}).drop(['PointID'], axis=1)

In [130]:
# ###import kx, ky
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'kPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'kx', 'y': 'ky'}).drop(['PointID'], axis=1)

In [131]:
# ###import lx, ly
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'lPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'lx', 'y': 'ly'}).drop(['PointID'], axis=1)


additional area calculations

In [132]:
#Calculate area of each area element based on i,j,k,l corner points and add 'Area' Column with computed area in default export units
df_areas[['ix', 'iy', 'jx', 'jy', 'kx', 'ky', 'lx', 'ly']] = df_areas[['ix', 'iy', 'jx', 'jy', 'kx', 'ky', 'lx', 'ly']].astype(float)
df_areas['Area'] =  0.5 * abs(df_areas['ix']*df_areas['jy'] + df_areas['jx']*df_areas['ky'] + df_areas['kx']*df_areas['ly'] + df_areas['lx']*df_areas['iy'] - (df_areas['iy']*df_areas['jx'] + df_areas['jy']*df_areas['kx'] + df_areas['ky']*df_areas['lx'] + df_areas['ly']*df_areas['ix']))

Define Deck Assignments

In [133]:
df = get_table('$ DECK PROPERTIES',filepath)
df = df[[1, 11, 13, 23]]
df = df.rename(columns={1: 'Section', 11: 'SlabDepth', 13: 'RibDepth', 23: 'DeckUnitWeight'})
df[['SlabDepth', 'RibDepth', 'DeckUnitWeight']] = df[['SlabDepth', 'RibDepth', 'DeckUnitWeight']].astype(float)
df_decksections = df

In [134]:
df_decksections

Section  SlabDepth  RibDepth  DeckUnitWeight
0    SD2+3.5-4KSI-NWC        3.5     2.000        0.000019
1    SD2+3.5-4KSI-LWC        3.0     2.000        0.000019
2    SD3+3.5-4KSI-NWC        3.5     3.000        0.000019
3      SD3+8-4KSI-NWC        8.0     3.000        0.000019
4    SD3+4.5-4KSI-NWC        4.5     3.000        0.000019
5  roof_deck_unfilled        8.0     2.625             NaN

In [135]:
df_areas

ElemID Level             Section ElemType iPointID jPointID kPointID  \
0       F1   L00              RS1-10    FLOOR        1        2        3   
1       F2   L00              RS1-10    FLOOR        5        6        7   
2       F3   L00              RS1-10    FLOOR        8        9       10   
3       F4   L00              RS1-10    FLOOR        9       11       12   
4       F5   L00              RS1-10    FLOOR       13       12       11   
..     ...   ...                 ...      ...      ...      ...      ...   
409   F166   L03  roof_deck_unfilled    FLOOR      130      131      146   
410   F167   L03  roof_deck_unfilled    FLOOR      147      146      131   
411   F168   L03  roof_deck_unfilled    FLOOR      133      148      147   
412   F169   L03  roof_deck_unfilled    FLOOR      149      148      133   
413   F170   L03  roof_deck_unfilled    FLOOR      108      109      124   

    lPointID        ix         iy        jx         jy        kx         ky  \
0          4 -5902.142 -5161.2230 -5902.142 -4771.2230 -6292.142 -4771.2230   
1          8 -6292.142 -4015.2230 -6292.142 -4393.2230 -5902.142 -4393.2230   
2          5 -5902.142 -4015.2230 -5902.142 -3637.2230 -6292.142 -3637.2230   
3         10 -5902.142 -3637.2230 -5902.142 -3259.2230 -6292.142 -3259.2230   
4         14 -6292.142 -2881.2230 -6292.142 -3259.2230 -5902.142 -3259.2230   
..       ...       ...        ...       ...        ...       ...        ...   
409      145 -5146.142 -1747.2230 -5146.142 -1369.2230 -5524.142 -1369.2230   
410      132 -5524.142  -991.2232 -5524.142 -1369.2230 -5146.142 -1369.2230   
411      132 -5146.142  -613.2232 -5524.142  -613.2232 -5524.142  -991.2232   
412      134 -5524.142  -235.2232 -5524.142  -613.2232 -5146.142  -613.2232   
413      123 -4768.142 -4393.2230 -4768.142 -4015.2230 -5146.142 -4015.2230   

           lx         ly         Area  
0   -6292.142 -5161.2230  152100.0000  
1   -5902.142 -4015.2230  147420.0000  
2   -6292.142 -4015.2230  147420.0000  
3   -6292.142 -3637.2230  147420.0000  
4   -5902.142 -2881.2230  147420.0000  
..        ...        ...          ...  
409 -5524.142 -1747.2230  142884.0000  
410 -5146.142  -991.2232  142883.9244  
411 -5146.142  -991.2232  142884.0000  
412 -5146.142  -235.2232  142884.0000  
413 -5146.142 -4393.2230  142884.0000  

[414 rows x 17 columns]

# Calculate Total Project Areas (Roper-Specific)



In [136]:
#get total project area in order to calculate PSF values

pv_PSF = pd.pivot_table(df_areas, values=(['Area']), index='Level', aggfunc='sum', margins = 'True', margins_name='Grand Total')
pv_PSF['Area (ft^2)'] = pv_PSF['Area']/144

# for Framed Area Values
suspended_slab_column= pv_PSF.columns.get_loc("Area (ft^2)"); suspended_slab_row= pv_PSF.index.get_loc("L00");
suspended_slab_ft= (int(math.ceil(pv_PSF.iat[suspended_slab_row,suspended_slab_column])))

total_area_column= pv_PSF.columns.get_loc("Area (ft^2)"); total_area_row= pv_PSF.index.get_loc("Grand Total");
total_area_ft= (int(math.ceil(pv_PSF.iat[total_area_row,total_area_column])))

slab_on_deck_ft = total_area_ft - suspended_slab_ft

In [137]:
print("total slab on deck (ft) =", slab_on_deck_ft)
print("total suspended slab (ft) =", suspended_slab_ft)
print("total framed area (ft) =", total_area_ft)


total slab on deck (ft) = 283801
total suspended slab (ft) = 124041
total framed area (ft) = 407842


# Calculate Frame Quantity Summaries (Roper-Specific)

## Generate Pivot Tables
>**pv_linesummary**: summary weights for system categories <br> **pv_brace**: summary info of BRB brace elements


pv_linesummary

In [138]:
#add total weight of member by multiplying unit weight (W) by length (Length)
df_lines['Weight'] = df_lines['W']*df_lines['Length'] #weight (kip/in)*(in)
#add column for category of group, ie. BRB.. = B, Gravity = G, Moment Frame = M
df_lines['Category'] = df_lines['Group'].str[0]

In [139]:
df_lines.drop(['MultiLevel','PointID_y','PointID_x','ix','iy','iz','jx','jy','jz','iPointID','jPointID'], axis=1)

ElemID Level      Section ElemType      Group AISC_Manual_Label    W  \
0        B1   L00  B24X24-6KSI     BEAM  Grade Bm.                 0  0.0   
1        B2   L00  B24X24-6KSI     BEAM  Grade Bm.                 0  0.0   
2        B3   L00  B24X24-6KSI     BEAM  Grade Bm.                 0  0.0   
3        B4   L00  B24X24-6KSI     BEAM  Grade Bm.                 0  0.0   
4        B5   L00  B24X24-6KSI     BEAM  Grade Bm.                 0  0.0   
...     ...   ...          ...      ...        ...               ...  ...   
2235    D74   L03        -7.85    BRACE        BRB                 0  0.0   
2236    D79   L03        -10.4    BRACE        BRB                 0  0.0   
2237    D80   L03        -10.4    BRACE        BRB                 0  0.0   
2238    D81   L03        -10.4    BRACE        BRB                 0  0.0   
2239    D82   L03        -10.4    BRACE        BRB                 0  0.0   

         _merge      Length  Weight Category  
0     left_only  324.000000     0.0        G  
1     left_only  378.000000     0.0        G  
2     left_only  378.000000     0.0        G  
3     left_only  378.001000     0.0        G  
4     left_only  378.000000     0.0        G  
...         ...         ...     ...      ...  
2235  left_only  305.484861     0.0        B  
2236  left_only  305.484737     0.0        B  
2237  left_only  305.484861     0.0        B  
2238  left_only  305.484861     0.0        B  
2239  left_only  305.484861     0.0        B  

[2240 rows x 11 columns]

In [140]:
#summary system weights (kip)
pv_linesummary = pd.pivot_table(df_lines, values='Weight', columns='ElemType', index='Category', aggfunc='sum', margins = 'True', margins_name='Grand Total').round(0)
# pv_linesummary = pv_linesummary.drop([('LINE'), ('BRACE')], axis=1).drop(('C'),axis=0).round(0)

In [141]:
pv_linesummary

ElemType       BEAM  BRACE  COLUMN  Grand Total
Category                                       
B             293.0    0.0   280.0        574.0
G            1687.0    NaN   336.0       2022.0
Grand Total  1980.0    0.0   616.0       2596.0

In [142]:
kip_to_tons = 0.5
kip_to_pounds = 1000

pv_linesummary['Beam (tons)'] = pv_linesummary['BEAM']*kip_to_tons
pv_linesummary['Column (tons)'] = pv_linesummary['COLUMN']*kip_to_tons
pv_linesummary['Total (tons)'] = pv_linesummary['Grand Total']*kip_to_tons

pv_linesummary['Beam (PSF)'] = pv_linesummary['BEAM']*kip_to_pounds/slab_on_deck_ft
pv_linesummary['Column (PSF)'] = pv_linesummary['COLUMN']*kip_to_pounds/slab_on_deck_ft
pv_linesummary['Total (PSF)'] = pv_linesummary['Grand Total']*kip_to_pounds/slab_on_deck_ft

pv_linesummary = pv_linesummary.drop(columns=['BEAM','COLUMN','Grand Total']).round(1)

pv_brace

In [143]:
pivot1 = df_lines[df_lines['Category'] == 'B']
pivot1 = pivot1[pivot1['ElemType'].str.contains('BR')]
#identify all the brb sizes by extracting portion of string that is a float
pivot1['BRBSize'] = pivot1['Section'].str.extract(r'(\d+)').astype(float)
pivot1['BRBDirection'] = pivot1['Group'].str[4]

#calculate BRB steel weight
steel_density = 0.284/1000 #kip/in^3
pivot1['BRBWeight'] = pivot1['BRBSize']*pivot1['Length']*steel_density

#create initial pivot table
pv_brace = pd.pivot_table(pivot1, values='BRBSize', columns='BRBDirection', index='Level', aggfunc='mean', margins = 'True', margins_name='Grand Total')

# # ~~~~this next line may not work once there is x and y - need to troubleshoot!
pv_brace = pv_brace.join(pd.pivot_table(pivot1, values = "Category", columns = "BRBDirection", index = 'Level', aggfunc ='count', margins = 'True', margins_name='Grand Total'),how='right', rsuffix='count')

#add weight from BRBs
pv_brace['Weight'] = pd.pivot_table(pivot1, values='BRBWeight', index='Level', aggfunc='sum',margins = 'True', margins_name='Grand Total').round(0)


<ipython-input-143-2235352d833d>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pivot1['BRBSize'] = pivot1['Section'].str.extract(r'(\d+)').astype(float)
<ipython-input-143-2235352d833d>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pivot1['BRBDirection'] = pivot1['Group'].str[4]
<ipython-input-143-2235352d833d>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: htt

In [144]:
# Additional Formatting

# Function to rename a column conditionally
def rename_column_if_exists(df, old_name, new_name):
    if old_name in df.columns:
        df = df.rename(columns={old_name: new_name})
    return df

# Function to delete last entry of column
def delete_last_entry(df, col_name):
    if col_name in df.columns:
          df.at[df.index[-1], col_name] = ""
    return df

columns_to_remove = [col for col in pv_brace.columns if col.startswith('Grand')]
pv_brace = pv_brace.drop(columns=columns_to_remove)

kip_to_tons = 0.5
pv_brace['Weight'] = pv_brace['Weight']*kip_to_tons
pv_brace = pv_brace.rename(columns={'Weight': 'Weight (tons)'})

# Rename the column if it exists and remove the averaged Grand Total values
pv_brace = rename_column_if_exists(pv_brace, 'X', 'X-Brace (in^2)')
pv_brace = delete_last_entry(pv_brace, 'X-Brace (in^2)')
pv_brace = rename_column_if_exists(pv_brace, 'Y', 'Y-Brace (in^2)')
pv_brace = delete_last_entry(pv_brace, 'Y-Brace (in^2)')

## Frame Summary Results

In [145]:
print("Summary weights (tons/PSF) per system *excluding BRB Core Sections*")
display(pv_linesummary)

print("BRB summary including count and weight (tons) per bracing direction")
display(pv_brace)

Summary weights (tons/PSF) per system *excluding BRB Core Sections*


ElemType     BRACE  Beam (tons)  Column (tons)  Total (tons)  Beam (PSF)  \
Category                                                                   
B              0.0        146.5          140.0         287.0         1.0   
G              NaN        843.5          168.0        1011.0         5.9   
Grand Total    0.0        990.0          308.0        1298.0         7.0   

ElemType     Column (PSF)  Total (PSF)  
Category                                
B                     1.0          2.0  
G                     1.2          7.1  
Grand Total           2.2          9.1

BRB summary including count and weight (tons) per bracing direction


BRBDirection  Weight (tons)
Level                      
L01                    74.5
L02                    68.5
L03                    20.5
Grand Total           163.5

#Calculate Area Quantities (Roper-Specific)

## Generate Pivot Tables

In [146]:
#calculate area element weight based on deck section assignment
df_areas = pd.merge(df_areas, df_decksections, on='Section')
concrete_density = 150/1000/(12*12*12) #150 lb/ft^3 converted to kip/in^3
# df_areas['Weight'] = df_areas['Area']*df_areas['UnitWeight']
df_areas['ConcreteWeight'] = df_areas['Area']*(df_areas['SlabDepth']+df_areas['RibDepth']/2)*concrete_density #wrong
df_areas['DeckWeight'] = df_areas['Area']*df_areas['DeckUnitWeight']

In [147]:
#summary system weights (kip)
pv_areasummary = pd.pivot_table(df_areas, values=(['Area','ConcreteWeight', 'DeckWeight']), index='Level', aggfunc='sum', margins = 'True', margins_name='Grand Total')
pv_areasummary['Area (ft^2)'] = pv_areasummary['Area']/144

pv_areasummary['Volume'] = pv_areasummary['ConcreteWeight']/concrete_density
pv_areasummary['Volume (ft^3)'] = pv_areasummary['Volume']/(12*12*12)

pv_areasummary = pv_areasummary.round(1)


In [148]:
pv_areasummary

Area  ConcreteWeight  DeckWeight  Area (ft^2)      Volume  \
Level                                                                         
L03          5143823.8          4158.1         0.0      35721.0  47901858.9   
Grand Total        0.0             0.0         0.0          0.0         0.0   

             Volume (ft^3)  
Level                       
L03                27721.0  
Grand Total            0.0

In [149]:
# Additional Formatting

#filter for relevant catagories
pv_areasummary2 = pv_areasummary.loc[:, ['Area (ft^2)', 'Volume (ft^3)','DeckWeight']]

#steel deck data
pv_areasummary2["Steel Deck Weight (tons)"] = pv_areasummary2["DeckWeight"]/2
pv_areasummary2 = pv_areasummary2.drop(columns=["DeckWeight"])

#concrete data
pv_areasummary2["Conc. Volume (CuY)"] = pv_areasummary2["Volume (ft^3)"]/27
pv_areasummary2 = pv_areasummary2.drop(columns=["Volume (ft^3)"])

# Keep only the first and last rows of the DataFrame, suspended slab is taken as equivalent as L01 with overridden concrete vol.
if len(pv_areasummary2) > 2:
    pv_areasummary2 = pd.concat([pv_areasummary2.iloc[[0]], pv_areasummary2.iloc[[-1]]])
elif len(pv_areasummary2) == 2:
    pv_areasummary2 = pv_areasummary2
elif len(pv_areasummary2) == 1:
    pv_areasummary2 = pv_areasummary2
else:
    print("DataFrame is empty")

pv_areasummary2 = pv_areasummary2.rename(index={"L01":"Suspended Slab", "Grand Total":"Slab on Deck"})

# Function to delete last entry of column
def delete_first_entry(df, col_name):
    if col_name in df.columns:
          df.at[df.index[0], col_name] = ""
    return df

# manually adjust the suspended slab data ... remove illogical steel deck weight in suspended slab (remaining from when we took L01 as suspended slab)
# pv_areasummary2 = delete_first_entry(pv_areasummary2, 'Steel Deck Weight (kip)')
pv_areasummary2.loc['Suspended Slab', 'Conc. Volume (CuY)'] = pv_areasummary2.loc['Suspended Slab', 'Area (ft^2)']/27 # to represent 1ft*area(ft) = 12" thick suspended slab
pv_areasummary2.loc['Suspended Slab', 'Steel Deck Weight (tons)'] = ""
# adjust rounding
pv_areasummary2 = pv_areasummary2.round(1)

KeyError: 'Suspended Slab'

In [150]:
# sqft = ([suspended_slab_ft,slab_on_deck_ft])
# sqft = pd.DataFrame(sqft)
# pv_areasummary2.join(sqft)

## Area Summary Results

In [151]:
print("Deck Area per floor (in^2) and Weights per Floor (kip)")
display(pv_areasummary2)

Deck Area per floor (in^2) and Weights per Floor (kip)


Area (ft^2)  Steel Deck Weight (tons)  Conc. Volume (CuY)
Level                                                                  
L03               35721.0                       0.0         1026.703704
Slab on Deck          0.0                       0.0            0.000000

# Format as HTML

In [152]:
# Function to format numbers with commas
def format_with_commas(x):
    if isinstance(x, (int, float)):
        return f"{x:,}"
    return x

info_brace = pv_brace.style.format(format_with_commas)
info_brace = info_brace.to_html(index=True)

info_frame = pv_linesummary.style.format(format_with_commas)
info_frame = info_frame.to_html(index=True)

info_area = pv_areasummary2.style.format(format_with_commas)
info_area = info_area.to_html(index=True)

# info_brace = pv_brace.to_html(index=True)
# info_frame = pv_linesummary.to_html(index=True)
# info_area = pv_areasummary.to_html(index=True)

# for Framed Area Results
slab_on_deck = "{:,}".format(int(slab_on_deck_ft))
suspended_slab = "{:,}".format(int(suspended_slab_ft))
total_area = "{:,}".format(int(total_area_ft))


In [153]:
combined_html = f"""

<html>
<head>
    <title>DataFrame Tables</title>
</head>
<body>

    <h1><b>{filepath}</b></h1>

    <h2><b>Framed Area</b></h2>
    <p style='display: inline;'>Slab on Deck: {slab_on_deck} ft<sup>2<sup><p>
    <p style='display: inline;'>Suspended Slab: {suspended_slab} ft<sup>2<sup><p>
    <p style='display: inline;'>Total Framed Area: {total_area} ft<sup>2<sup><p>

    <h1>Frame Info</h1>
    {info_frame}
    <h1>Brace Info</h1>
    {info_brace}
    <h1>Area Info</h1>
    {info_area}


</body>
</html>
"""

# Final Report

In [154]:
# Step 4: Write the combined HTML to a file
with open('/content/dataframes.html', 'w') as f:
    f.write(combined_html)

# Step 5: Display the HTML file in Colab
display(HTML(combined_html))

# Send To Excel


In [ ]:
# with pd.ExcelWriter('Template_Quantities.xlsx') as writer:
#   pv_areasummary.to_excel(writer, sheet_name='area_pivot_table', index=False)
#   pv_linesummary.to_excel(writer, sheet_name='frame_pivot_table', index=False)
#   pv_brace.to_excel(writer, sheet_name='brb_pivot_table', index=False)

In [ ]:
# with pd.ExcelWriter(
#     'Template_Quantities.xlsx',
#     mode="a",
#     engine="openpyxl",
#     if_sheet_exists="overlay",
# ) as writer:
#     pv_areasummary.to_excel(writer, sheet_name='area_pivot_table', index=True)
#     pv_linesummary.to_excel(writer, sheet_name='frame_pivot_table', index=True)
#     pv_brace.to_excel(writer, sheet_name='brb_pivot_table', index=True)

# Import Column Joint Reactions

In [ ]:
file_path = "testbasereactions.xlsx"

#######evaluate units more carefully for the excel sheet - or make sure they are exported to access using the right units!
# Read the first two rows to get headers and sub-headers
headers = pd.read_excel(file_path, header=[1])

# Read the actual data, skipping the first two rows used for headers
df_jointreactions = pd.read_excel(file_path, skiprows=[0, 1,2])

# Set the MultiIndex columns
df_jointreactions.columns = headers.columns

df_jointreactions

In [ ]:
pv_jointsummarymax = pd.pivot_table(df_jointreactions, values=['FZ'], columns=['Label'], index = ['Output Case'], aggfunc=['max'])  #, margins = 'True', margins_name='Grand Total'
pv_jointsummarymin = pd.pivot_table(df_jointreactions, values=['FZ'], columns=['Label'], index = ['Output Case'], aggfunc=['min'])  #, margins = 'True', margins_name='Grand Total'



In [ ]:
pv_jointsummarymin